# MMAction2 Tutorial

- 用MMAction2的识别模型做一次推理
- 用新数据集训练一个新的识别模型
- 用MMAction2的时空检测模型做一次推理

## 安装 MMAction2

In [ ]:
# 查看环境中pytorch版本以便mmcv对应版本下载
!pip list | grep torch

torch                         1.8.1+cu101        
torchsummary                  1.5.1              
torchtext                     0.9.1              
torchvision                   0.9.1+cu101        


In [ ]:
# 安装mmcv-full，注意需要对应pytorch1.8和cuda10.1版本
!pip install mmcv-full -f https://download.openmmlab.com/mmcv/dist/cu101/torch1.8.0/index.html

Looking in links: https://download.openmmlab.com/mmcv/dist/cu101/torch1.8.0/index.html
     |████████████████████████████████| 31.2MB 96kB/s 
     |████████████████████████████████| 194kB 7.7MB/s 


In [ ]:
# 克隆mmaction2项目
# %cd /content/
# !rm -rf mmaction2
# !git clone https://github.com/open-mmlab/mmaction2.git
!git clone https://github.com/wangruohui/mmaction2.git
%cd /content/mmaction2
!git checkout fix_nms_config

# 以可编辑的模式安装mmaction
!pip install -e .

# 安装一些额外的依赖
!pip install -r requirements/optional.txt

Cloning into 'mmaction2'...
remote: Enumerating objects: 11360, done.
remote: Counting objects: 100% (1029/1029), done.
remote: Compressing objects: 100% (587/587), done.
remote: Total 11360 (delta 603), reused 721 (delta 436), pack-reused 10331
Receiving objects: 100% (11360/11360), 37.17 MiB | 14.99 MiB/s, done.
Resolving deltas: 100% (7930/7930), done.
/content/mmaction2
Branch 'fix_nms_config' set up to track remote branch 'fix_nms_config' from 'origin'.
Switched to a new branch 'fix_nms_config'
Obtaining file:///content/mmaction2
  Running setup.py develop for mmaction2
     |████████████████████████████████| 37.2MB 81kB/s 
     |████████████████████████████████| 14.1MB 225kB/s 
     |████████████████████████████████| 12.2MB 26.1MB/s 
     |████████████████████████████████| 4.5MB 35.9MB/s 
  Created wheel for PyTurboJPEG: filename=PyTurboJPEG-1.5.0-cp37-none-any.whl size=7478 sha256=ea928a968966ea04f37722e3866c986be613835f0598c242df7e44e6e9d6749b
  Stored in directory: /root/.cach

In [ ]:
# 检查torch的安装以及gpu的使用
import torch, torchvision
print(torch.__version__, torch.cuda.is_available())

# 检查MMAction2的安装
import mmaction
print(mmaction.__version__)

# 检查mmcv的安装
from mmcv.ops import get_compiling_cuda_version, get_compiler_version
print(get_compiling_cuda_version())
print(get_compiler_version())

1.8.1+cu101 True
0.15.0
10.1
GCC 7.3


## MMAction2识别模型的推理

In [ ]:
# 创建checkpoints文件夹并下载tsn模型
!mkdir checkpoints
!wget -c https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth \
      -O checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth

--2021-06-03 15:01:35--  https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth
Resolving download.openmmlab.com (download.openmmlab.com)... 47.88.36.78
Connecting to download.openmmlab.com (download.openmmlab.com)|47.88.36.78|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 97579339 (93M) [application/octet-stream]
Saving to: ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’

checkpoints/tsn_r50 100%[===================>]  93.06M  11.1MB/s    in 8.2s    

2021-06-03 15:01:44 (11.4 MB/s) - ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’ saved [97579339/97579339]



In [ ]:
from mmaction.apis import inference_recognizer, init_recognizer

# 选择tsn对应的配置文件
config = 'configs/recognition/tsn/tsn_r50_video_inference_1x1x3_100e_kinetics400_rgb.py'
# 加载上面下载的checkpoint文件
checkpoint = 'checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'
# 初始化模型
model = init_recognizer(config, checkpoint, device='cuda:0')

In [ ]:
# 选择视频进行推理
video = 'demo/demo.mp4'
label = 'demo/label_map_k400.txt'
results = inference_recognizer(model, video, label)

In [ ]:
# 查看视频
from IPython.display import HTML
from base64 import b64encode
mp4 = open(video,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)

In [ ]:
# 查看推理Top-5结果
for result in results:
    print(f'{result[0]}: ', result[1])

## 在自定义数据集上训练模型
训练新模型通常有三个步骤:
- 支持新数据集
- 修改配置文件
- 训练模型


### 支持新数据集

这里我们给出将数据转换为已有数据集格式的示例。其他方法可以参考[doc](/docs/tutorials/new_dataset.md)

用到的是一个从[Kinetics-400](https://deepmind.com/research/open-source/open-source-datasets/kinetics/)中获取的tiny数据集。包含30个训练视频，10个测试视频。

In [ ]:
# 下载并解压数据集kinetics400_tiny
!rm kinetics400_tiny.zip*
!rm -rf kinetics400_tiny
!wget https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
!unzip kinetics400_tiny.zip > /dev/null

rm: cannot remove 'kinetics400_tiny.zip*': No such file or directory
--2021-06-03 14:55:03--  https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
Resolving download.openmmlab.com (download.openmmlab.com)... 47.88.36.78
Connecting to download.openmmlab.com (download.openmmlab.com)|47.88.36.78|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 18308682 (17M) [application/zip]
Saving to: ‘kinetics400_tiny.zip’

kinetics400_tiny.zi 100%[===================>]  17.46M  10.5MB/s    in 1.7s    

2021-06-03 14:55:07 (10.5 MB/s) - ‘kinetics400_tiny.zip’ saved [18308682/18308682]



In [ ]:
# 安装tree工具并检查数据集目录结构
!apt-get -q install tree
!tree kinetics400_tiny

In [ ]:
# 查看标注文件格式
!cat kinetics400_tiny/kinetics_tiny_train_video.txt

根据[`VideoDataset`](./datasets/video_dataset.py)中定义的格式，每一行表示样本视频的文件名和标签，用空格符分隔。


### 修改配置文件

我们需要修改配置文件，同时会用到之前下载的checkpoint作为pre-trained模型。


In [ ]:
# 获得tsn对应的配置文件cfg
from mmcv import Config
cfg = Config.fromfile('./configs/recognition/tsn/tsn_r50_video_1x1x8_100e_kinetics400_rgb.py')

我们在原本用于kinetics400-full数据集训练的tsn模型配置上进行修改，让模型可以在Kinetics400-tiny数据集上进行训练。



In [ ]:
from mmcv.runner import set_random_seed

# 修改数据集类型和各个文件路径
cfg.dataset_type = 'VideoDataset'
cfg.data_root = 'kinetics400_tiny/train/'
cfg.data_root_val = 'kinetics400_tiny/val/'
cfg.ann_file_train = 'kinetics400_tiny/kinetics_tiny_train_video.txt'
cfg.ann_file_val = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.ann_file_test = 'kinetics400_tiny/kinetics_tiny_val_video.txt'

cfg.data.test.type = 'VideoDataset'
cfg.data.test.ann_file = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.data.test.data_prefix = 'kinetics400_tiny/val/'

cfg.data.train.type = 'VideoDataset'
cfg.data.train.ann_file = 'kinetics400_tiny/kinetics_tiny_train_video.txt'
cfg.data.train.data_prefix = 'kinetics400_tiny/train/'

cfg.data.val.type = 'VideoDataset'
cfg.data.val.ann_file = 'kinetics400_tiny/kinetics_tiny_val_video.txt'
cfg.data.val.data_prefix = 'kinetics400_tiny/val/'

# 这里用于确认是否使用到omnisource训练
cfg.setdefault('omnisource', False)
# 修改cls_head中类别数为2
cfg.model.cls_head.num_classes = 2
# 使用预训练好的tsn模型
cfg.load_from = './checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'

# 设置工作目录
cfg.work_dir = './tutorial_exps'

# 由于是单卡训练，修改对应的lr
cfg.data.videos_per_gpu = cfg.data.videos_per_gpu // 16
cfg.optimizer.lr = cfg.optimizer.lr / 8 / 16
cfg.total_epochs = 30

# 设置存档点间隔减少存储空间的消耗
cfg.checkpoint_config.interval = 10
# 设置日志打印间隔减少打印时间
cfg.log_config.interval = 5

# 固定随机种子使得结果可复现
cfg.seed = 0
set_random_seed(0, deterministic=False)
cfg.gpu_ids = range(1)

# 打印所有的配置参数
print(f'Config:\n{cfg.pretty_text}')


Config:
model = dict(
    type='Recognizer2D',
    backbone=dict(
        type='ResNet',
        pretrained='torchvision://resnet50',
        depth=50,
        norm_eval=False),
    cls_head=dict(
        type='TSNHead',
        num_classes=2,
        in_channels=2048,
        spatial_type='avg',
        consensus=dict(type='AvgConsensus', dim=1),
        dropout_ratio=0.4,
        init_std=0.01),
    train_cfg=None,
    test_cfg=dict(average_clips=None))
optimizer = dict(type='SGD', lr=7.8125e-05, momentum=0.9, weight_decay=0.0001)
optimizer_config = dict(grad_clip=dict(max_norm=40, norm_type=2))
lr_config = dict(policy='step', step=[40, 80])
total_epochs = 30
checkpoint_config = dict(interval=10)
log_config = dict(interval=5, hooks=[dict(type='TextLoggerHook')])
dist_params = dict(backend='nccl')
log_level = 'INFO'
load_from = './checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'
resume_from = None
workflow = [('train', 1)]
dataset_type = 'VideoDataset'
data_root =

### 训练识别模型


In [ ]:
import os.path as osp

from mmaction.datasets import build_dataset
from mmaction.models import build_model
from mmaction.apis import train_model

import mmcv

# 构建数据集
datasets = [build_dataset(cfg.data.train)]

# 构建动作识别模型
model = build_model(cfg.model, train_cfg=cfg.get('train_cfg'), test_cfg=cfg.get('test_cfg'))

# 创建工作目录并训练模型
mmcv.mkdir_or_exist(osp.abspath(cfg.work_dir))
train_model(model, datasets, cfg, distributed=False, validate=True)

Use load_from_torchvision loader


Downloading: "https://download.pytorch.org/models/resnet50-19c8e357.pth" to /root/.cache/torch/hub/checkpoints/resnet50-19c8e357.pth


2021-06-03 15:02:48,410 - mmaction - INFO - These parameters in pretrained checkpoint are not loaded: {'fc.bias', 'fc.weight'}
/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))
2021-06-03 15:02:59,146 - mmaction - INFO - load checkpoint from ./checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth
2021-06-03 15:02:59,147 - mmaction - INFO - Use load_from_local loader
2021-06-03 15:02:59,233 - mmaction - WARNING - The model and loaded state dict do not match exactly

size mismatch for cls_head.fc_cls.weight: copying a param with shape torch.Size([400, 2048]) from checkpoint,

[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 5.7 task/s, elapsed: 2s, ETA:     0s

2021-06-03 15:03:32,826 - mmaction - INFO - Evaluating top_k_accuracy ...
2021-06-03 15:03:32,828 - mmaction - INFO - 
top1_acc	0.8000
top5_acc	1.0000
2021-06-03 15:03:32,831 - mmaction - INFO - Evaluating mean_class_accuracy ...
2021-06-03 15:03:32,836 - mmaction - INFO - 
mean_acc	0.8000
2021-06-03 15:03:33,250 - mmaction - INFO - Now best checkpoint is saved as best_top1_acc_epoch_5.pth.
2021-06-03 15:03:33,251 - mmaction - INFO - Best top1_acc is 0.8000 at 5 epoch.
2021-06-03 15:03:33,255 - mmaction - INFO - Epoch(val) [5][5]	top1_acc: 0.8000, top5_acc: 1.0000, mean_class_accuracy: 0.8000
2021-06-03 15:03:37,510 - mmaction - INFO - Epoch [6][5/15]	lr: 7.813e-05, eta: 0:02:44, time: 0.848, data_time: 0.638, memory: 1654, top1_acc: 0.8000, top5_acc: 1.0000, loss_cls: 0.5897, loss: 0.5897, grad_norm: 11.0816
2021-06-03 15:03:38,830 - mmaction - INFO - Epoch [6][10/15]	lr: 7.813e-05, eta: 0:02:38, time: 0.266, data_time: 0.094, memory: 1654, top1_acc: 0.6000, top5_acc: 1.0000, loss_cls

...

2021-06-03 15:05:14,159 - mmaction - INFO - Evaluating top_k_accuracy ...
2021-06-03 15:05:14,161 - mmaction - INFO - 
top1_acc	1.0000
top5_acc	1.0000
2021-06-03 15:05:14,166 - mmaction - INFO - Evaluating mean_class_accuracy ...
2021-06-03 15:05:14,168 - mmaction - INFO - 
mean_acc	1.0000
2021-06-03 15:05:14,599 - mmaction - INFO - Now best checkpoint is saved as best_top1_acc_epoch_20.pth.
2021-06-03 15:05:14,603 - mmaction - INFO - Best top1_acc is 1.0000 at 20 epoch.
2021-06-03 15:05:14,606 - mmaction - INFO - Saving checkpoint at 20 epochs
2021-06-03 15:05:15,008 - mmaction - INFO - Epoch(val) [20][5]	top1_acc: 1.0000, top5_acc: 1.0000, mean_class_accuracy: 1.0000
2021-06-03 15:05:19,127 - mmaction - INFO - Epoch [21][5/15]	lr: 7.813e-05, eta: 0:01:01, time: 0.823, data_time: 0.618, memory: 1654, top1_acc: 0.8000, top5_acc: 1.0000, loss_cls: 0.3904, loss: 0.3904, grad_norm: 7.6698
2021-06-03 15:05:20,196 - mmaction - INFO - Epoch [21][10/15]	lr: 7.813e-05, eta: 0:00:58, time: 0.21

[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 5.8 task/s, elapsed: 2s, ETA:     0s

2021-06-03 15:05:49,031 - mmaction - INFO - Evaluating top_k_accuracy ...
2021-06-03 15:05:49,033 - mmaction - INFO - 
top1_acc	0.8000
top5_acc	1.0000
2021-06-03 15:05:49,039 - mmaction - INFO - Evaluating mean_class_accuracy ...
2021-06-03 15:05:49,040 - mmaction - INFO - 
mean_acc	0.8000
2021-06-03 15:05:49,042 - mmaction - INFO - Epoch(val) [25][5]	top1_acc: 0.8000, top5_acc: 1.0000, mean_class_accuracy: 0.8000
2021-06-03 15:05:53,064 - mmaction - INFO - Epoch [26][5/15]	lr: 7.813e-05, eta: 0:00:29, time: 0.801, data_time: 0.590, memory: 1654, top1_acc: 0.9000, top5_acc: 1.0000, loss_cls: 0.3512, loss: 0.3512, grad_norm: 7.0619
2021-06-03 15:05:54,188 - mmaction - INFO - Epoch [26][10/15]	lr: 7.813e-05, eta: 0:00:27, time: 0.225, data_time: 0.030, memory: 1654, top1_acc: 0.9000, top5_acc: 1.0000, loss_cls: 0.3328, loss: 0.3328, grad_norm: 7.1553
2021-06-03 15:05:55,139 - mmaction - INFO - Epoch [26][15/15]	lr: 7.813e-05, eta: 0:00:25, time: 0.192, data_time: 0.018, memory: 1654, top

[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 5.8 task/s, elapsed: 2s, ETA:     0s

2021-06-03 15:06:22,740 - mmaction - INFO - Evaluating top_k_accuracy ...
2021-06-03 15:06:22,742 - mmaction - INFO - 
top1_acc	1.0000
top5_acc	1.0000
2021-06-03 15:06:22,746 - mmaction - INFO - Evaluating mean_class_accuracy ...
2021-06-03 15:06:22,747 - mmaction - INFO - 
mean_acc	1.0000
2021-06-03 15:06:22,756 - mmaction - INFO - Saving checkpoint at 30 epochs
2021-06-03 15:06:23,168 - mmaction - INFO - Epoch(val) [30][5]	top1_acc: 1.0000, top5_acc: 1.0000, mean_class_accuracy: 1.0000


## 评价模型


In [ ]:
from mmaction.apis import single_gpu_test
from mmaction.datasets import build_dataloader
from mmcv.parallel import MMDataParallel

# 构建测试数据集
dataset = build_dataset(cfg.data.test, dict(test_mode=True))
data_loader = build_dataloader(
        dataset,
        videos_per_gpu=1,
        workers_per_gpu=cfg.data.workers_per_gpu,
        dist=False,
        shuffle=False)
model = MMDataParallel(model, device_ids=[0])
outputs = single_gpu_test(model, data_loader)

# 在测试集上评价训练完成的识别模型
eval_config = cfg.evaluation
eval_config.pop('interval')
eval_res = dataset.evaluate(outputs, **eval_config)
for name, val in eval_res.items():
    print(f'{name}: {val:.04f}')

[                                                  ] 0/10, elapsed: 0s, ETA:

/usr/local/lib/python3.7/dist-packages/torch/utils/data/dataloader.py:477: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  cpuset_checked))


[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 10/10, 2.2 task/s, elapsed: 4s, ETA:     0s
Evaluating top_k_accuracy ...

top1_acc	0.9000
top5_acc	1.0000

Evaluating mean_class_accuracy ...

mean_acc	0.9000
top1_acc: 0.9000
top5_acc: 1.0000
mean_class_accuracy: 0.9000


## 时空动作识别

这里我们用到mmdet来辅助完成时空动作识别的任务，首先要在主目录下进行安装。

In [ ]:
# 克隆mmdetection项目
%cd ..
!git clone https://github.com/open-mmlab/mmdetection.git
%cd mmdetection

# 以可编辑的模式安装mmdet
!pip install -e .
%cd ../mmaction2

/content
Cloning into 'mmdetection'...
remote: Enumerating objects: 18118, done.
remote: Counting objects: 100% (207/207), done.
remote: Compressing objects: 100% (163/163), done.
remote: Total 18118 (delta 87), reused 113 (delta 44), pack-reused 17911
Receiving objects: 100% (18118/18118), 21.50 MiB | 33.66 MiB/s, done.
Resolving deltas: 100% (12576/12576), done.
/content/mmdetection
Obtaining file:///content/mmdetection
  Created wheel for terminaltables: filename=terminaltables-3.1.0-cp37-none-any.whl size=15356 sha256=37a2b87aceff6ca4b32508fac67142e960106f99a33a0a1d2127aaaecd9fae0b
  Stored in directory: /root/.cache/pip/wheels/30/6b/50/6c75775b681fb36cdfac7f19799888ef9d8813aff9e379663e
Successfully built terminaltables
  Running setup.py develop for mmdet
/content/mmaction2


同时我们需要上传视频至目录mmaction2下

In [ ]:
!wget https://download.openmmlab.com/mmaction/dataset/sample/1j20qq1JyX4.mp4 -O demo/1j20qq1JyX4.mp4

In [ ]:
# 完成时空检测
!python demo/demo_spatiotemporal_det.py --video demo/1j20qq1JyX4.mp4

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)2826240/45929032 bytes (6.2%)6922240/45929032 bytes (15.1%)10977280/45929032 bytes (23.9%)14925824/45929032 bytes (32.5%)19046400/45929032 bytes (41.5%)23068672/45929032 bytes (50.2%)26279936/45929032 bytes (57.2%)30392320/45929032 bytes (66.2%)34471936/45929032 bytes (75.1%)38543360/45929032 bytes (83.9%)42688512/45929032 bytes (92.9%)45929032/45929032 bytes (100.0%)
  Done
File saved as /root

In [ ]:
# 查看视频
from IPython.display import HTML
from base64 import b64encode
mp4 = open('demo/stdet_demo.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=400 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)